![image](https://cdn.discordapp.com/attachments/996200880351215636/1065002848355631165/New_Atlantis.png)

---
# [HUMANN-3 Pipeline] Next generation unified metabolic analysis network

## Next generation unified metabolic analysis network
---

```
HUMAnN is a pipeline for efficiently and accurately profiling the presence/absence and abundance of microbial pathways in a community from metagenomic or metatranscriptomic sequencing data (typically millions of short DNA/RNA reads). This process, referred to as functional profiling, aims to describe the metabolic potential of a microbial community and its members. More generally, functional profiling answers the question "What are the microbes in my community-of-interest doing (or capable of doing)?"
```
---
[Github for HUMANN-3](https://github.com/biobakery/humann)

#### Described in the following paper: [Marine microbial metagenomes sampled across space and time](https://www.nature.com/articles/sdata2018176)


## Title and Overview 

### Abstract from the Paper:

Recent advances in understanding the ecology of marine systems have been greatly facilitated by the growing availability of metagenomic data, which provide information on the identity, diversity and functional potential of the microbial community in a particular place and time. Here we present a dataset comprising over 5 terabases of metagenomic data from 610 samples spanning diverse regions of the Atlantic and Pacific Oceans. One set of metagenomes, collected on GEOTRACES cruises, captures large geographic transects at multiple depths per station. The second set represents two years of time-series data, collected at roughly monthly intervals from 3 depths at two long-term ocean sampling sites, Station ALOHA and BATS. These metagenomes contain genomic information from a diverse range of bacteria, archaea, eukaryotes and viruses. The data’s utility is strengthened by the availability of extensive physical, chemical, and biological measurements associated with each sample. We expect that these metagenomes will facilitate a wide range of comparative studies that seek to illuminate new aspects of marine microbial ecosystems.

ALOHA Station:
    The ALOHA Station is a research facility located in the North Pacific Ocean that is used for studying marine microbial communities and their role in biogeochemical cycles.

The station is named after the ALOHA (A Long-term Oligotrophic Habitat Assessment) site, which is a region of the ocean characterized by low nutrient levels and high microbial diversity. The ALOHA Station is equipped with a variety of instruments and sensors that allow researchers to collect and analyze data on the physical, chemical, and biological properties of the ocean.

In the context of metagenomic research, the ALOHA Station has been used to study the microbial communities present in the North Pacific Ocean and their functional potential. Researchers have used metagenomic sequencing to analyze the genetic material obtained from the microbial communities and identify the functional pathways and metabolic processes that are present.

By studying the microbial communities at the ALOHA Station, researchers can gain insights into the role of marine microbes in global biogeochemical cycles, such as carbon and nitrogen cycling, and their potential impact on climate change. The ALOHA Station is an important resource for metagenomic research and provides a unique opportunity to study the microbial communities in one of the most oligotrophic regions of the ocean.

## Code Imports 

In [2]:
!pip install -r Bacalhau_Demo_Data/requirements_nb1.txt -q

In [3]:
!pip install geopandas -q
!pip install ipywidgets -q
!pip install import-ipynb -q

In [4]:
import import_ipynb
from Bacalhau_Demo_Data.Utility_Funcs import *

import_dependencies()

importing Jupyter notebook from /home/jovyan/shared/material/Protocols/MetaGenome_Alpha/Bacalhau_Demo_Data/Utility_Funcs.ipynb


True

### Import Statements 

In [5]:
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
from matplotlib import cm
import seaborn as sns
import colorsys
from matplotlib.collections import PatchCollection
import Bio.SeqIO as bioseqio
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
    #from Bio.Alphabet import IUPAC
from Bio import Entrez
from ete3 import NCBITaxa
from taxonomy_ranks import TaxonomyRanks
from subprocess import Popen, call, STDOUT, PIPE
import os
import shutil
import pandas as pd
import numpy as np
import matplotlib
import json
import glob
import re
import gzip
import sys
import csv
import time
import io
import pathlib
from collections import OrderedDict
import configparser
import pickle
import bz2 
from IPython.display import Image
from itertools import combinations
import itertools
import ipyleaflet as mep 
import geopandas as gpd 
import ipywidgets as widgets  

## MetaData Map for MetaGenomic Sample Locations

### Generate Data Set

In [6]:
meta_csv = pd.read_csv("Bacalhau_Demo_Data/geotraces_samples_max_10mts_depth.csv")
locations = meta_csv["Latitude and Longitude"]
longitude = locations.astype(str).apply(lambda row: ' '.join(row.split(' ')[2:]))
latitude = locations.astype(str).apply(lambda row: ' '.join(row.split(' ')[0:2]))
meta_csv['Longitude'] = longitude.astype(str).apply(long_convert)
meta_csv['Latitude'] = latitude.astype(str).apply(lat_convert)
#meta_csv.columns

### Map Utility

In [7]:
def make_map(meta_df, data_type):
    countries = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))
    
    geo_df = gpd.GeoDataFrame(meta_df, geometry = gpd.points_from_xy(meta_df.Longitude, meta_df.Latitude))

    m = mep.Map(center=(0,-75), zoom = 1.8, basemap = mep.basemaps.Esri.WorldTopoMap)

    geo_data = mep.GeoData(geo_dataframe = countries,
                   style={'color': 'black', 'fillColor': '#2D5A27', 'opacity':0.05, 'weight':1.9, 'dashArray':'2', 'fillOpacity':0.6},
                   hover_style={'fillColor': 'red' , 'fillOpacity': 0.2},
                   name = 'Countries')

    tara_data = mep.GeoData(geo_dataframe = geo_df,
                    style = {'color':'red', 'fillColor':'#ff0000','opacity' : 1, 'fill_opacity':1},
                    title = geo_df['Sample name'],
                    point_style={'radius': 5, 'color': 'red', 'fillOpacity': 1, 'fillColor': 'blue', 'weight': 2},
                    hover_style={'fillColor':'yellow', 'fillOpacity':0.3},
                    name = 'Meta')
    locations = [] 
    for i in range(len(meta_df.Longitude)):
        locations += [[meta_df.Longitude.iloc[i], meta_df.Latitude.iloc[i]]]
    
    boat_icon = mep.AwesomeIcon(
        name = 'ship',
        marker_color = 'blue',
        icon_color = 'black',
        spin = False)

    aloha_icon = mep.AwesomeIcon(
        name = 'ship',
        marker_color = 'pink',
        icon_color = 'blue',
        spin = False)

    for i in range(len(locations)):
        loc = locations[i]
        if meta_csv['Cruise series'].iloc[i].strip() == 'HOT':
            marker = mep.Marker(icon = aloha_icon, location = (loc[1], loc[0]), title = str(meta_csv[data_type].iloc[i]), opacity = 1)
        else:
            marker = mep.Marker(icon = boat_icon, location = (loc[1], loc[0]), title = str(meta_csv[data_type].iloc[i]), opacity = 1)
        m.add_layer(marker)


    m.add_layer(geo_data)
    m.add_layer(tara_data)
    m.add_control(mep.LayersControl())

    
    return m 
    


### Display Map and MetaData

In [8]:
drop = widgets.Dropdown(
    options = ['Sample name', 'Cruise series', 'Collection Date', 'Depth (m)', 'env_biome','Latitude and Longitude','Total read pairs','Assembly method and version'],
    #value = 'Sample name',
    description = 'Meta Data:',
    disabled = False,)

out = widgets.Output()

def on_button(b):
    with out:
        out.clear_output(wait = True)
        meta_data = drop.value
        mp = make_map(meta_csv, meta_data)
        display(mp)
        print("Clicked")
        
b_layout = widgets.Layout(height='40px', min_width='140px')
butt = widgets.Button(layout=b_layout, description="Display Map", button_style='warning')

butt.on_click(on_button)
display(drop, butt, out)


Dropdown(description='Meta Data:', options=('Sample name', 'Cruise series', 'Collection Date', 'Depth (m)', 'e…

Button(button_style='warning', description='Display Map', layout=Layout(height='40px', min_width='140px'), sty…

Output()

### Pivot Table 

In [9]:
!pip install pivottablejs -q 

In [10]:
from pivottablejs import pivot_ui 

In [11]:
pivot_ui(meta_csv)

## Humann3 - Functional Pathways and Taxonomic Assignment

### Introduction and Summary 

#### What is the HUMAnN Algorithm?

HUMAnN, standing for the HMP Unified Metabolic Analysis Network, comes from the Huttenhower Lab under the Department of Biostatistics at Harvard. HUMAnN is a method for profiling the abundance of different microbial metabolic pathways or other molecular functions from metagenonmic sequence data using comprehensive refernce databases. The HUMAnN algorithm analyzes the read of all the genetic data from a sample of ocean water to derive which microbial species are present and the functional pathways of the ecosystem, meaning which biochemical prcoesses occur in the ecosystem and their relative abundance. 

#### Functional Pathways

One key insight that HUMAnN hopes to generate are the functional pathways of the microbial ecosystem being analyzed. A functional pathway refers to the series of biochemical reactions that occur within a cell or organism to perform a specific biologic function, an example of which being the ingestion of oxygen and exhaliation of carbon dioxide in human respiration or photosynthesis. Evaluating the functional pathways of an ecosystem is important because these pathways produce the nutrients that sustain larger organisms, other microbes and perform other essential functions such as capturing carbon. Understanding the functional potential of plankton in particular is invaluable to understanding the functional biodiversity and environmental potential of the oceans. 

Example Functional Pathway: Photosynthesis     
![image](https://cdn.discordapp.com/attachments/1067186538762485962/1087825445447270431/image.png)

#### Understanding the Data

The input to the HUMANnN 3.0 algorithm are metagenomic raw reads, simply consisting of long sequences of genetic data extracted from the ocean and read together, commonly store in the FASTQ file format 

There are three main outputs of the HUMAnN algorithm that we are to be analyzing herein:

-Gene Families 
-Pathway Abundance 
-Pathway Coverage

The gene families identifes the relative abundance of different clusters of genes found within the metagenomic sample associated organism lineages.
Pathway abundance determines the relative abundance of different metabolic pathways identified within the metagenomic sample, this illustates the capbilitity of the ecosystem to consume and process different sources of energy or molecules found in the environment, such as carbon.
Pathway coverage is a useful metric to determine at a very high level the abundance of a fully described metabolic pathway. Coverage attempts to quantify the certainty of the pathway abundance based on the depth and wuality of the metagenomic data.

### Processing HUMAnN 3.0 Results for the ALOHA Station

The following code will take the outputs of the HUMAnN 3.0 algorithm run on a collection of metgenomic samples from the ALOHA station.

#### Top Line Package Parameters

In [12]:
data_path = './Bacalhau_Demo_Data'
pd.set_option('mode.chained_assignment', None)
matplotlib.rcParams['savefig.dpi'] = 1000
matplotlib.rcParams['figure.dpi'] = 1000
sns.set_style("whitegrid", {'axes.grid' : False})
sns.set_context("paper")
sns.set(font='serif')
sns.set_style('ticks')

#### Load Metadata from a the Aloha Metagenomic Samples

Explanation of the data set and SSR_IDs

In [13]:
#loads meta data from local files 
aloha_metadata, ssr_ids = load_Metadata()
display(aloha_metadata.head())

Total number of samples processed by HUMANN: 18


Sample name Cruise series GEOTRACES section Cruise ID Cruise Station  \
0       S0501           HOT               NaN    HOT156  Station ALOHA   
1       S0502           HOT               NaN    HOT156  Station ALOHA   
2       S0503           HOT               NaN    HOT156  Station ALOHA   
3       S0504           HOT               NaN    HOT158  Station ALOHA   
4       S0505           HOT               NaN    HOT158  Station ALOHA   

  Collection Date Depth (m)    env_biome env_feature env_material  ...  \
0      2004-02-24         4  ocean_biome       ocean        water  ...   
1      2004-02-24      98,7  ocean_biome       ocean        water  ...   
2      2004-02-24     173,3  ocean_biome       ocean        water  ...   
3      2004-04-20      23,8  ocean_biome       ocean        water  ...   
4      2004-04-20     124,4  ocean_biome       ocean        water  ...   

    Bottle ID NCBI BioProject  NCBI SRA Study NCBI BioSample  \
0  1560200314     PRJNA385855       SRP109831   SAMN07136998   
1  1560200308     PRJNA385855       SRP109831   SAMN07136999   
2  1560200304     PRJNA385855       SRP109831   SAMN07137000   
3  1580200313     PRJNA385855       SRP109831   SAMN07137001   
4  1580200306     PRJNA385855       SRP109831   SAMN07137002   

  NCBI SRA Accession Total read pairs  Total bases  \
0         SRR5720299         13333617   4000085100   
1         SRR5720300         10540927   3162278100   
2         SRR5720301         12242781   3672834300   
3         SRR5720302         41507610  12452283000   
4         SRR5720303         26554323   7966296900   

   NCBI SRA Accession for assembled metagenome contigs  \
0                                          SRZ187079     
1                                          SRZ187080     
2                                          SRZ187081     
3                                          SRZ187082     
4                                          SRZ187083     

   Assembly method and version Unnamed: 21  
0            metaSPAdes v3.9.0         NaN  
1            metaSPAdes v3.9.0         NaN  
2            metaSPAdes v3.9.0         NaN  
3           metaSPAdes v3.10.1         NaN  
4            metaSPAdes v3.9.0         NaN  

[5 rows x 22 columns]

#### Sort and Organize metadata by Date 

Given a file containing the metadata of every sample referenced, we will isolate the those from the ALOHA station that were processed via the HUMAnN algorithm. These samples will then be chronologically sorted.

In [14]:
#imported from submodule 
aloha_time_series, dates = construct_time_series(aloha_metadata, ssr_ids)

display(aloha_time_series.head())

Sample name Cruise series GEOTRACES section Cruise ID Cruise Station  \
27       S0528           HOT               NaN    HOT144  Station ALOHA   
30       S0531           HOT               NaN    HOT145  Station ALOHA   
33       S0534           HOT               NaN    HOT146  Station ALOHA   
36       S0537           HOT               NaN    HOT147  Station ALOHA   
39       S0540           HOT               NaN    HOT148  Station ALOHA   

   Collection Date Depth (m)    env_biome env_feature env_material  ...  \
27      2003-01-17       4,4  ocean_biome       ocean        water  ...   
30      2003-02-25       4,3  ocean_biome       ocean        water  ...   
33      2003-03-28       8,3  ocean_biome       ocean        water  ...   
36      2003-04-23       4,3  ocean_biome       ocean        water  ...   
39      2003-05-20       4,4  ocean_biome       ocean        water  ...   

     Bottle ID NCBI BioProject  NCBI SRA Study NCBI BioSample  \
27  1440200914     PRJNA385855       SRP109831   SAMN07137025   
30  1450200318     PRJNA385855       SRP109831   SAMN07137028   
33  1460200314     PRJNA385855       SRP109831   SAMN07137031   
36  1470200314     PRJNA385855       SRP109831   SAMN07137034   
39  1480200316     PRJNA385855       SRP109831   SAMN07137037   

   NCBI SRA Accession Total read pairs Total bases  \
27         SRR5720247         26441873  7932561900   
30         SRR5720269         17902513  5370753900   
33         SRR5720268         17826774  5348032200   
36         SRR5720271         25313647  7594094100   
39         SRR5720266         23802307  7140692100   

    NCBI SRA Accession for assembled metagenome contigs  \
27                                          SRZ187106     
30                                          SRZ187109     
33                                          SRZ187112     
36                                          SRZ187115     
39                                          SRZ187118     

    Assembly method and version Unnamed: 21  
27            metaSPAdes v3.9.0         NaN  
30            metaSPAdes v3.9.0         NaN  
33            metaSPAdes v3.9.0         NaN  
36            metaSPAdes v3.9.0         NaN  
39            metaSPAdes v3.9.0         NaN  

[5 rows x 22 columns]

#### Load and Process HUMAnN 3.0 Results 

##### DataTransform for Visualization

The pathway abundance results from HUMAnN 3.0 are loaded into a dataframe where some preliminary data cleaning is performed to removed null values and reformat the pathway names to a more readable format.

Define what filtering and stratification does.

In [15]:
humann_path = os.path.join(data_path,'joint_samples_path_abundance-cpm.tsv')

stratified_df, filtered_df = generate_stratified(humann_path, aloha_time_series, dates)

community_abundance = generate_community_abundance(filtered_df, aloha_time_series, dates)

##### Visualizing Community Aggregated Metabolic pathway abundances through time 

The following steps will clean the data slightly more and make it suitable to be visualized.

In [16]:
threshholded_logged_community_abund = thresh_and_log(community_abundance, 0.25)

In [17]:
threshholded_logged_community_abund.head(5)

Week:3 (2003)  \
PathwayID                                                           
VALSYN-PWY: L-valine biosynthesis                        2.991518   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...       2.986270   
PWY-5103: L-isoleucine biosynthesis III                  2.976968   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...       2.978386   
NONOXIPENT-PWY: pentose phosphate pathway (non-...       2.943974   

                                                    Week:9 (2003)  \
PathwayID                                                           
VALSYN-PWY: L-valine biosynthesis                        3.009952   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...       3.009710   
PWY-5103: L-isoleucine biosynthesis III                  3.004351   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...       3.001037   
NONOXIPENT-PWY: pentose phosphate pathway (non-...       2.970125   

                                                    Week:13 (2003)  \
PathwayID                                                            
VALSYN-PWY: L-valine biosynthesis                         3.007551   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...        3.006496   
PWY-5103: L-isoleucine biosynthesis III                   3.000664   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...        2.999190   
NONOXIPENT-PWY: pentose phosphate pathway (non-...        2.931063   

                                                    Week:17 (2003)  \
PathwayID                                                            
VALSYN-PWY: L-valine biosynthesis                         2.944937   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...        2.944342   
PWY-5103: L-isoleucine biosynthesis III                   2.936719   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...        2.939294   
NONOXIPENT-PWY: pentose phosphate pathway (non-...        2.883841   

                                                    Week:21 (2003)  \
PathwayID                                                            
VALSYN-PWY: L-valine biosynthesis                         3.004274   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...        3.002999   
PWY-5103: L-isoleucine biosynthesis III                   2.995391   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...        2.998929   
NONOXIPENT-PWY: pentose phosphate pathway (non-...        2.953757   

                                                    Week:25 (2003)  \
PathwayID                                                            
VALSYN-PWY: L-valine biosynthesis                         2.952400   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...        2.943255   
PWY-5103: L-isoleucine biosynthesis III                   2.928716   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...        2.928189   
NONOXIPENT-PWY: pentose phosphate pathway (non-...        2.757860   

                                                    Week:29 (2003)  \
PathwayID                                                            
VALSYN-PWY: L-valine biosynthesis                         3.062202   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...        3.053217   
PWY-5103: L-isoleucine biosynthesis III                   3.045037   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...        3.044975   
NONOXIPENT-PWY: pentose phosphate pathway (non-...        2.960315   

                                                    Week:34 (2003)  \
PathwayID                                                            
VALSYN-PWY: L-valine biosynthesis                         3.009952   
ILEUSYN-PWY: L-isoleucine biosynthesis I (from ...        3.004996   
PWY-5103: L-isoleucine biosynthesis III                   2.996608   
BRANCHED-CHAIN-AA-SYN-PWY: superpathway of bran...        2.993446   
NONOXIPENT-PWY: pentose phosphate pathway (non-...        2.921235   

                                                    Week:45 (2003)  \
PathwayID                                                           

##### Create a Clustermap of the Results 

In [18]:
#To display the whole clustermap uncomment below


#"""g = sns.clustermap(threshholded_logged_community_abund,
#                   method='ward',
#                    metric='euclidean',
#                    col_cluster=False,
#                    vmin=threshholded_logged_community_abund.values.ravel().min(), 
#                    vmax=threshholded_logged_community_abund.values.ravel().max(), 
#                    cmap=plt.cm.Reds, 
#                    yticklabels=True, 
#                    linewidth=1, 
#                    linecolor="white",
#                    figsize=(40,30),
#                    dendrogram_ratio=0.15,
#                    cbar_pos=None,
#                    cbar_kws=dict(ticks=[0, 0.50, 1], orientation='ver')
#                   )

#g.cax.set_visible(False)
#g.ax_heatmap.set_yticklabels(g.ax_heatmap.get_yticklabels(), fontsize=9)

#print('Done!')"""


In [19]:
#g.savefig('clustermap.png', dpi=300, bbox_inches='tight')
#plt.close(g.fig)

In [20]:
#plt.savefig(f'./Bacalhau_Demo_Data/Clustermaps/clustermap_full.png', dpi=300, bbox_inches='tight')
#plt.close(g.fig)

In [21]:
def cluster_plot(df, title, fig_size = (40,30)):
    plot = sns.clustermap(df,
                    method='ward',
                    metric='euclidean',
                    col_cluster=False,
                    vmin=df.values.ravel().min(), 
                    vmax=df.values.ravel().max(), 
                    cmap=plt.cm.Reds, 
                    yticklabels=True, 
                    linewidth=1, 
                    linecolor="white",
                    figsize=fig_size,
                    dendrogram_ratio=0.15,
                    cbar_pos=None,
                    cbar_kws=dict(ticks=[0, 0.50, 1], orientation='ver')
                   )
#   plt.style.use("dark_background")
    #g.cax.set_visible(False)
    plot.ax_heatmap.set_yticklabels(plot.ax_heatmap.get_yticklabels(), fontsize=9)
    plot.savefig(f'./Bacalhau_Demo_Data/Clustermaps/clustermap_{title}.png', dpi=300, bbox_inches='tight')
    #plt.close(g.fig)
    
    return f'./Bacalhau_Demo_Data/Clustermaps/clustermap_{title}.png'

##### Functional Pathway Clustermap


A figure like this provides a high-level summary of the combination of metabolic pathways 
(and their relative abundances within a community) encoded in the genome of a great variety 
of species found in oceaninc water samples. Importantly, the clustergram provides an idea of 
the similarity between different species in terms of metabolic pathway profiles. Overall, this
information provides a fundamental window into the metabolic diversity and potential of a 
marine microbiome, which is arguably a critical factor determining the health and biogeochemical
capacities of the base layers of the entire marine trophic interaction network, the planktonic
ecosystem. 

This feature matrix derived from marine metagenomics data analysis is a major component of our marine biodiversity asset enginering 
pipeline. In a nutshell, this data structure is being used to prototype numerous multidimensional functional diversity metrics, which
hold great potential as compact quantitative readouts of the metabolic health of the marine microbiome. 

In [22]:
display(Image(filename = './Bacalhau_Demo_Data/old_Clustermaps/clustermap.png'))

##### Time Series Accordian 

In [23]:
object_fit = 'none'
from ipywidgets import Layout, Button, VBox, Label
from IPython.display import display as Display

outputs = widgets.Output()

def on_button_clicked(b):
    with outputs:
        outputs.clear_output(wait = True)
        print(b.description)
        title = b.description
        if os.path.exists(f'./Bacalhau_Demo_Data/Clustermaps/clustermap_{title}.png'):
            display(Image(filename = f'./Bacalhau_Demo_Data/Clustermaps/clustermap_{title}.png'))
            
        else:
            plot = cluster_plot(threshholded_logged_community_abund[b.description], b.description, (12,35))
            display(Image(filename=plot))
        


item_layout = Layout(height='40px', min_width='140px')
items = [Button(layout=item_layout, description=i, button_style='warning') for i in threshholded_logged_community_abund.columns.to_list()]
for j in items:
    j.on_click(on_button_clicked)
box_layout = Layout(overflow='scroll hidden',
                    border='3px solid black',
                    width='1100px',
                    height='',
                    flex_flow='row',
                    display='flex')
carousel = VBox(children=items, layout=box_layout)
VBox([Label('Metagenomic Samples:'), carousel])

display(carousel, outputs)

payload = VBox(children=[carousel, outputs])


Output()

In [24]:
print(os.path.exists('./Bacalhau_Demo_Data/Clustermaps/clustermap.png'))

False


In [25]:
#!/usr/bin/env bash
#curl -L ftp://ftp.sra.ebi.ac.uk/vol1/fastq/SRR572/006/SRR5720246/SRR5720246_1.fastq.gz -o SRR5720246_Metagenome_from_Station_ALOHA_HOT166_5m_1.fastq.gz
#curl -L ftp://ftp.sra.ebi.ac.uk/vol1/fastq/SRR572/006/SRR5720246/SRR5720246_2.fastq.gz -o SRR5720246_Metagenome_from_Station_ALOHA_HOT166_5m_2.fastq.gz

# DEMO ZONE

In [26]:
import ipywidgets as widgets
from IPython.display import display
import requests

# Replace these URLs with your own
logo_url = 'https://cdn.discordapp.com/attachments/996200880351215636/1065002848355631165/New_Atlantis.png'
google_drive_shareable_link = 'https://drive.google.com/file/d/1T6He3Mqz4l_Etp72to6cUSBRCKo-Xyek/view?usp=sharing'  # Replace with your shareable link

logo = widgets.Image(value=requests.get(logo_url).content, format='png')

# Extract the file ID from the Google Drive shareable link
file_id = google_drive_shareable_link.split('/d/')[1].split('/view')[0]

# Create the Google Drive embedded viewer URL
google_drive_embed_url = f'https://drive.google.com/file/d/{file_id}/preview'

iframe_code = f'<iframe src="{google_drive_embed_url}" width="100%" height="600" frameborder="0" allowfullscreen webkitallowfullscreen msallowfullscreen></iframe>'
presentation = widgets.HTML(value=iframe_code)
vbox = widgets.VBox([logo, presentation])

In [27]:
# Widget Section 1

# Import / Init
import ipywidgets as widgets

# Layout
# item_layout = widgets.layout(height='100px', min_width='40px')
options_list = list(ssr_ids)
# Create the widgets
ms_dropdown = widgets.Dropdown(
    options= options_list,
    # value='2',
    description='NewAtlantis Datasets:',
    disabled=False,
    style={'description_width': 'initial'})  # Set the description_width style to 'initial'


ms_url_supply = widgets.Text(
    value='Hello World',
    placeholder='Type something',
    description='Dataset URL:',
    disabled=False
)

ms_file_upload = widgets.FileUpload(
    description='Dataset Upload:')


# Create the tab contents
tab_contents = ['NewAtlantis Datasets', 'Select Dataset', 'Upload Dataset']
children = [widgets.Box([ms_dropdown]), widgets.Box([ms_url_supply]), widgets.Box([ms_file_upload])]

# Create the tab widget
tab = widgets.Tab()
tab.children = children
tab.titles = tab_contents

tab.set_title(0, "NewAtlantis Dataset")
tab.set_title(1, "Host Dataset")
tab.set_title(2, "Upload Dataset")

In [28]:
# Widget Section 2

!pip install pivottablejs -q

from pivottablejs import pivot_ui 
import pandas as pd
from ipywidgets import Output
import IPython.display as display

from IPython.display import HTML, display

dark_mode_css = """
<style>
    .pvtTable {
        background-color: #222;
        color: white;
    }
    .pvtTable thead th,
    .pvtTable tbody th {
        background-color: #333;
    }
    .pvtTable td {
        background-color: #444;
    }
    .pvtTable tr:hover td {
        background-color: #555;
    }
</style>
"""

display(HTML(dark_mode_css))

def lat_convert(lat:str):
    values = lat.split(' ')
    if values[1].strip() == 'S':
        return -float(values[0])
    else:
        return float(values[0])
    
def long_convert(long:str):
    values = long.split(' ')
    if values[1].strip() == 'W':
        return -float(values[0])
    else:
        return float(values[0])
    

meta_csv = pd.read_csv("geotraces_samples_max_10mts_depth.csv")
locations = meta_csv["Latitude and Longitude"]
longitude = locations.astype(str).apply(lambda row: ' '.join(row.split(' ')[2:]))
latitude = locations.astype(str).apply(lambda row: ' '.join(row.split(' ')[0:2]))
meta_csv['Longitude'] = longitude.astype(str).apply(long_convert)
meta_csv['Latitude'] = latitude.astype(str).apply(lat_convert)



pivotBox = Output()
with pivotBox:
    display(pivot_ui(meta_csv))

In [29]:
# Widget Section 3
# Milestone 3 Elements

'''
TODO:

- Add a Bacalhau control interface
    - Be able to configure and run a protocol
    - Add a few options with the main selection being the metagenome alpha 
- Adapt the map and map interace to our dataset
- switch out the temp rain graphs for the gene cluster map
'''


# Map Making
from ipyleaflet import Map, basemaps, basemap_to_tiles, Heatmap, TileLayer
from ipywidgets import AppLayout
from ipywidgets import HTML, Layout, Dropdown, Output, Textarea, VBox, Label
import bqplot as bq
import numpy as np
from pandas import date_range

OWM_API_KEY = "94192e4fadd8cf660dd02719ae92d65e" #openweathermap API key

m = make_map(meta_csv, 'Sample name')


maps = {'Mapnik' : basemaps.OpenStreetMap.Mapnik,
        'Esri' : basemaps.Esri.DeLorme}

header = HTML("<h1>Metagenome Data Atlas</h1>", layout=Layout(height='auto'))
header.style.text_align='center'
basemap_selector = Dropdown( options = list(maps.keys()),
                           layout=Layout(width='auto'))

heatmap_selector = Dropdown(options=('Temperature', 'Precipitation'),
                            layout=Layout(width='auto'))

basemap_selector.value = 'Mapnik'
m.layout.height='600px'
security_1 = np.cumsum(np.random.randn(150)) + 100.

dates = date_range(start='01-01-2007', periods=150)

dt_x = bq.DateScale()
sc_y = bq.LinearScale()

time_series = bq.Lines(x=dates, y=security_1, scales={'x': dt_x, 'y': sc_y})
ax_x = bq.Axis(scale=dt_x)
ax_y = bq.Axis(scale=sc_y, orientation='vertical')

fig = bq.Figure(marks=[time_series], axes=[ax_x, ax_y],
                fig_margin=dict(top=0, bottom=80, left=30, right=20))

m.layout.width='auto'
m.layout.height='auto'
fig.layout.width='auto'
fig.layout.height='auto'

out = HTML(
    value='',
    layout=Layout(width='auto', height='auto')
)

mapBox = AppLayout(center=m, 
          header=header,
#          left_sidebar=VBox([Label("Basemap:"),
#                             basemap_selector,
#                             Label("Overlay:"),
#                             heatmap_selector]),
          right_sidebar=fig,
          footer=out,
          pane_widths=['80px', 1, 1],
          pane_heights=['80px', 4, 1],
          height='600px',
          grid_gap="30px")


# Interaction Function
rows = []

X, Y = np.mgrid[-90:90:10j, -180:180:20j]

X = X.flatten()
Y = Y.flatten()

temps = np.random.randn(200, 150)*0.5

from datetime import datetime

import random

def add_log(msg):
    max_rows = 3
    rows.append(msg)
    if len(rows) > max_rows:
        rows.pop(0)
    return '<h4>Activity log</h4><ul>{}</ul>'.format('<li>'.join([''] + rows))

def generate_temp_series(x, y):
    if heatmap_selector.value == 'Precipitation':
        temp = np.cumsum(np.random.randn(150)) + 100.
    elif heatmap_selector.value == 'Temperature':
        dist = np.sqrt((X - x)**2 + (Y-y)**2) / 100
        dist = dist.max() - dist
        dist[dist > np.percentile(dist, 5)] = 0
        temp = np.cumsum(np.dot(dist, temps)+0.05) + 20 - np.abs(x) / 2
    time_series.y = temp
    
def handle_interaction(**kwargs):
    if kwargs['type'] == 'click':
        generate_temp_series(*kwargs['coordinates'])
        msg = '%s Selected coordinates: %s, Temp: %d C Precipitation: %d mm\n' % (
            datetime.now(), kwargs['coordinates'], random.randint(-20, 20), random.randint(0, 100))
        out.value = add_log(msg)

m.on_interaction(handle_interaction) 

def on_map_selected(change):
    m.layers = [basemap_to_tiles(maps[basemap_selector.value]), weather_maps[heatmap_selector.value]]
    
basemap_selector.observe(on_map_selected, names='value')
heatmap_selector.observe(on_map_selected, names='value')

temp = TileLayer(min_zoom=1, max_zoom=18, url='https://tile.openweathermap.org/map/temp_new/{z}/{x}/{y}.png?appid='+OWM_API_KEY, name='owm', attribute='me')
precipitation = TileLayer(min_zoom=1, max_zoom=18, url='https://tile.openweathermap.org/map/precipitation_new/{z}/{x}/{y}.png?appid='+OWM_API_KEY, name='owm', attribute='me')

weather_maps = {'Temperature' : temp,
                'Precipitation' : precipitation}

m.add_layer(weather_maps[heatmap_selector.value])


# DEMO SHOW

In [30]:
# Demo Accordion
# Workbench

import ipywidgets as widgets

kelvin_map = make_map(meta_csv, 'Sample name')

accordion = widgets.Accordion(children=[vbox, tab, mapBox, payload])

accordion.set_title(0, "Presentation")
accordion.set_title(1, "Data Selection")
accordion.set_title(2, "Data Atlas")
accordion.set_title(3, "HUMANN Container Runtime")

accordion

Accordion(children=(VBox(children=(Image(value=b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x02\xff\x00\x00\x…